## About Dataset
Context
This is a small subset of dataset of Book reviews from Amazon Kindle Store category.

Content
5-core dataset of product reviews from Amazon Kindle Store category from May 1996 - July 2014. Contains total of 982619 entries. Each reviewer has at least 5 reviews and each product has at least 5 reviews in this dataset.
Columns

- asin - ID of the product, like B000FA64PK
- helpful - helpfulness rating of the review - example: 2/3.
- overall - rating of the product.
- reviewText - text of the review (heading).
- reviewTime - time of the review (raw).
- reviewerID - ID of the reviewer, like A3SPTOKDG7WBLN
- reviewerName - name of the reviewer.
- summary - summary of the review (description).
- unixReviewTime - unix timestamp.

Acknowledgements
This dataset is taken from Amazon product data, Julian McAuley, UCSD website. http://jmcauley.ucsd.edu/data/amazon/

License to the data files belong to them.

Inspiration
- Sentiment analysis on reviews.
- Understanding how people rate usefulness of a review/ What factors influence helpfulness of a review.
- Fake reviews/ outliers.
- Best rated product IDs, or similarity between products based on reviews alone (not the best idea ikr).
- Any other interesting analysis

#### Best Practises
1. Preprocessing And Cleaning
2. Train Test Split
3. BOW,TFIDF,Word2vec
4. Train ML algorithms

In [1]:
# Load the dataset
import pandas as pd
data=pd.read_csv('Kindle Reviews/all_kindle_review.csv')
data.head()

Unnamed: 0.1  Unnamed: 0        asin  helpful  rating  \
0             0       11539  B0033UV8HI  [8, 10]       3   
1             1        5957  B002HJV4DE   [1, 1]       5   
2             2        9146  B002ZG96I4   [0, 0]       3   
3             3        7038  B002QHWOEU   [1, 3]       3   
4             4        1776  B001A06VJ8   [0, 1]       4   

                                          reviewText   reviewTime  \
0  Jace Rankin may be short, but he's nothing to ...   09 2, 2010   
1  Great short read.  I didn't want to put it dow...   10 8, 2013   
2  I'll start by saying this is the first of four...  04 11, 2014   
3  Aggie is Angela Lansbury who carries pocketboo...   07 5, 2014   
4  I did not expect this type of book to be in li...  12 31, 2012   

       reviewerID  reviewerName                   summary  unixReviewTime  
0  A3HHXRELK8BHQG        Ridley  Entertaining But Average      1283385600  
1  A2RGNZ0TRF578I  Holly Butler   Terrific menage scenes!      1381190400  
2  A3S0H2HV6U1I7F       Merissa          Snapdragon Alley      1397174400  
3   AC4OQW3GZ919J    Cleargrace    very light murder cozy      1404518400  
4  A3C9V987IQHOQD      Rjostler                      Book      1356912000

In [2]:
df=data[['reviewText','rating']]
df.head()

reviewText  rating
0  Jace Rankin may be short, but he's nothing to ...       3
1  Great short read.  I didn't want to put it dow...       5
2  I'll start by saying this is the first of four...       3
3  Aggie is Angela Lansbury who carries pocketboo...       3
4  I did not expect this type of book to be in li...       4

In [3]:
df.shape

(12000, 2)

In [4]:
## Missing Values
df.isnull().sum()

reviewText    0
rating        0
dtype: int64

In [5]:
df['rating'].unique()

array([3, 5, 4, 2, 1])

In [6]:
df['rating'].value_counts()

rating
5    3000
4    3000
3    2000
2    2000
1    2000
Name: count, dtype: int64

In [7]:
## Preprocessing And Cleaning

In [8]:
## postive review is 1 and negative review is 0
df['rating']=df['rating'].apply(lambda x:0 if x<3 else 1)

/var/folders/hj/8fxfbdp516z1q9b5vhdr9yq00000gn/T/ipykernel_14618/3208188810.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['rating']=df['rating'].apply(lambda x:0 if x<3 else 1)


In [9]:
df['rating'].value_counts()

rating
1    8000
0    4000
Name: count, dtype: int64

In [10]:
## 1. Lower All the cases
df['reviewText']=df['reviewText'].str.lower()

/var/folders/hj/8fxfbdp516z1q9b5vhdr9yq00000gn/T/ipykernel_14618/1654308119.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['reviewText']=df['reviewText'].str.lower()


In [11]:
df.head()

reviewText  rating
0  jace rankin may be short, but he's nothing to ...       1
1  great short read.  i didn't want to put it dow...       1
2  i'll start by saying this is the first of four...       1
3  aggie is angela lansbury who carries pocketboo...       1
4  i did not expect this type of book to be in li...       1

In [12]:
import re
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/anurag2/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [13]:
from bs4 import BeautifulSoup
import lxml

In [14]:
## Removing special characters
df['reviewText']=df['reviewText'].apply(lambda x:re.sub('[^a-z A-z 0-9-]+', '',x))
## Remove the stopswords
df['reviewText']=df['reviewText'].apply(lambda x:" ".join([y for y in x.split() if y not in stopwords.words('english')]))
## Remove url 
df['reviewText']=df['reviewText'].apply(lambda x: re.sub(r'(http|https|ftp|ssh)://([\w_-]+(?:(?:\.[\w_-]+)+))([\w.,@?^=%&:/~+#-]*[\w@?^=%&/~+#-])?', '' , str(x)))
## Remove html tags
df['reviewText']=df['reviewText'].apply(lambda x: BeautifulSoup(x, 'lxml').get_text())
## Remove any additional spaces
df['reviewText']=df['reviewText'].apply(lambda x: " ".join(x.split()))


/var/folders/hj/8fxfbdp516z1q9b5vhdr9yq00000gn/T/ipykernel_14618/1658462958.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['reviewText']=df['reviewText'].apply(lambda x:re.sub('[^a-z A-z 0-9-]+', '',x))
/var/folders/hj/8fxfbdp516z1q9b5vhdr9yq00000gn/T/ipykernel_14618/1658462958.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['reviewText']=df['reviewText'].apply(lambda x:" ".join([y for y in x.split() if y not in stopwords.words('english')]))
/var/folders/hj/8fxfbdp516z1q9b5vhdr9yq00000gn/T/ip

In [15]:
df.head()

reviewText  rating
0  jace rankin may short hes nothing mess man hau...       1
1  great short read didnt want put read one sitti...       1
2  ill start saying first four books wasnt expect...       1
3  aggie angela lansbury carries pocketbooks inst...       1
4  expect type book library pleased find price right       1

In [16]:
## Lemmatizer
from nltk.stem import WordNetLemmatizer

In [17]:
lemmatizer=WordNetLemmatizer()

In [18]:
def lemmatize_words(text):
    return " ".join([lemmatizer.lemmatize(word) for word in text.split()])


In [19]:
df['reviewText']=df['reviewText'].apply(lambda x:lemmatize_words(x))

/var/folders/hj/8fxfbdp516z1q9b5vhdr9yq00000gn/T/ipykernel_14618/1959687590.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['reviewText']=df['reviewText'].apply(lambda x:lemmatize_words(x))


In [20]:
df.head()

reviewText  rating
0  jace rankin may short he nothing mess man haul...       1
1  great short read didnt want put read one sitti...       1
2  ill start saying first four book wasnt expecti...       1
3  aggie angela lansbury carry pocketbook instead...       1
4  expect type book library pleased find price right       1

In [21]:
## Train Test Split
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(df['reviewText'],df['rating'],
                                              test_size=0.20)

In [22]:
from sklearn.feature_extraction.text import CountVectorizer
bow=CountVectorizer()
X_train_bow=bow.fit_transform(X_train).toarray()
X_test_bow=bow.transform(X_test).toarray()

In [23]:
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf=TfidfVectorizer()
X_train_tfidf=tfidf.fit_transform(X_train).toarray()
X_test_tfidf=tfidf.transform(X_test).toarray()

In [24]:
X_train_bow

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [25]:
from sklearn.naive_bayes import GaussianNB
nb_model_bow=GaussianNB().fit(X_train_bow,y_train)
nb_model_tfidf=GaussianNB().fit(X_train_tfidf,y_train)

In [26]:
from sklearn.metrics import confusion_matrix,accuracy_score,classification_report

In [27]:
y_pred_bow=nb_model_bow.predict(X_test_bow)

In [28]:
y_pred_tfidf=nb_model_bow.predict(X_test_tfidf)

In [29]:
confusion_matrix(y_test,y_pred_bow)

array([[533, 290],
       [699, 878]])

In [30]:
print("BOW accuracy: ",accuracy_score(y_test,y_pred_bow))

BOW accuracy:  0.5879166666666666


In [31]:
confusion_matrix(y_test,y_pred_tfidf)

array([[521, 302],
       [694, 883]])

In [32]:
print("TFIDF accuracy: ",accuracy_score(y_test,y_pred_tfidf))

TFIDF accuracy:  0.585


In [33]:
import gensim
from gensim.models import Word2Vec, KeyedVectors
import gensim.downloader as api

wv = api.load('word2vec-google-news-300')


In [50]:
wv['king']

array([ 1.25976562e-01,  2.97851562e-02,  8.60595703e-03,  1.39648438e-01,
       -2.56347656e-02, -3.61328125e-02,  1.11816406e-01, -1.98242188e-01,
        5.12695312e-02,  3.63281250e-01, -2.42187500e-01, -3.02734375e-01,
       -1.77734375e-01, -2.49023438e-02, -1.67968750e-01, -1.69921875e-01,
        3.46679688e-02,  5.21850586e-03,  4.63867188e-02,  1.28906250e-01,
        1.36718750e-01,  1.12792969e-01,  5.95703125e-02,  1.36718750e-01,
        1.01074219e-01, -1.76757812e-01, -2.51953125e-01,  5.98144531e-02,
        3.41796875e-01, -3.11279297e-02,  1.04492188e-01,  6.17675781e-02,
        1.24511719e-01,  4.00390625e-01, -3.22265625e-01,  8.39843750e-02,
        3.90625000e-02,  5.85937500e-03,  7.03125000e-02,  1.72851562e-01,
        1.38671875e-01, -2.31445312e-01,  2.83203125e-01,  1.42578125e-01,
        3.41796875e-01, -2.39257812e-02, -1.09863281e-01,  3.32031250e-02,
       -5.46875000e-02,  1.53198242e-02, -1.62109375e-01,  1.58203125e-01,
       -2.59765625e-01,  

In [35]:
df

reviewText  rating
0      jace rankin may short he nothing mess man haul...       1
1      great short read didnt want put read one sitti...       1
2      ill start saying first four book wasnt expecti...       1
3      aggie angela lansbury carry pocketbook instead...       1
4      expect type book library pleased find price right       1
...                                                  ...     ...
11995  valentine cupid vampire- jena ian another vamp...       1
11996  read seven book series apocalypticadventure on...       1
11997  book really wasnt cuppa situation man capturin...       1
11998  tried use charge kindle didnt even register ch...       0
11999  taking instruction look often hidden world sex...       1

[12000 rows x 2 columns]

In [36]:
df.shape

(12000, 2)

In [37]:
len(df)

12000

In [42]:
corpus= []
for i in range(0,len(df)):
    txt=df['reviewText'].iloc[i]
    corpus.append(txt)

corpus


['jace rankin may short he nothing mess man hauled saloon undertaker know he famous bounty hunter oregon 1890s shot man saloon finished year long quest avenge sister murder trying figure next snotty-nosed farm boy rescued gang bully offer money kill man forced ranch reluctantly agrees bring man justice kill outright first need tell sister widower newskyla kyle springer bailey riding trail sleeping ground past month trying find jace want revenge man killed husband took ranch amongst crime shes keen detour jace want take realizes shes option hide behind boy persona best try keep pace confrontation along way get shot jace discovers kyles kyla come clean whole reason need scoundrel dead hope hell still help herthe book share touching moment slow-blooming romance kyla find good reason fear men hide behind boy persona watching jace slowly pull shell help conquer fear endearing pain real deeply-rooted didnt disappear face sexiness neither understandable aversion marriage magically disappear r

In [43]:
from nltk import sent_tokenize
from gensim.utils import simple_preprocess

In [44]:
words=[]
for sent in corpus:
    sent_token=sent_tokenize(sent)
    for sent in sent_token:
        words.append(simple_preprocess(sent))


words

[['jace',
  'rankin',
  'may',
  'short',
  'he',
  'nothing',
  'mess',
  'man',
  'hauled',
  'saloon',
  'undertaker',
  'know',
  'he',
  'famous',
  'bounty',
  'hunter',
  'oregon',
  'shot',
  'man',
  'saloon',
  'finished',
  'year',
  'long',
  'quest',
  'avenge',
  'sister',
  'murder',
  'trying',
  'figure',
  'next',
  'snotty',
  'nosed',
  'farm',
  'boy',
  'rescued',
  'gang',
  'bully',
  'offer',
  'money',
  'kill',
  'man',
  'forced',
  'ranch',
  'reluctantly',
  'agrees',
  'bring',
  'man',
  'justice',
  'kill',
  'outright',
  'first',
  'need',
  'tell',
  'sister',
  'widower',
  'newskyla',
  'kyle',
  'springer',
  'bailey',
  'riding',
  'trail',
  'sleeping',
  'ground',
  'past',
  'month',
  'trying',
  'find',
  'jace',
  'want',
  'revenge',
  'man',
  'killed',
  'husband',
  'took',
  'ranch',
  'amongst',
  'crime',
  'shes',
  'keen',
  'detour',
  'jace',
  'want',
  'take',
  'realizes',
  'shes',
  'option',
  'hide',
  'behind',
  'boy',
 

In [55]:
words[0]

['jace',
 'rankin',
 'may',
 'short',
 'he',
 'nothing',
 'mess',
 'man',
 'hauled',
 'saloon',
 'undertaker',
 'know',
 'he',
 'famous',
 'bounty',
 'hunter',
 'oregon',
 'shot',
 'man',
 'saloon',
 'finished',
 'year',
 'long',
 'quest',
 'avenge',
 'sister',
 'murder',
 'trying',
 'figure',
 'next',
 'snotty',
 'nosed',
 'farm',
 'boy',
 'rescued',
 'gang',
 'bully',
 'offer',
 'money',
 'kill',
 'man',
 'forced',
 'ranch',
 'reluctantly',
 'agrees',
 'bring',
 'man',
 'justice',
 'kill',
 'outright',
 'first',
 'need',
 'tell',
 'sister',
 'widower',
 'newskyla',
 'kyle',
 'springer',
 'bailey',
 'riding',
 'trail',
 'sleeping',
 'ground',
 'past',
 'month',
 'trying',
 'find',
 'jace',
 'want',
 'revenge',
 'man',
 'killed',
 'husband',
 'took',
 'ranch',
 'amongst',
 'crime',
 'shes',
 'keen',
 'detour',
 'jace',
 'want',
 'take',
 'realizes',
 'shes',
 'option',
 'hide',
 'behind',
 'boy',
 'persona',
 'best',
 'try',
 'keep',
 'pace',
 'confrontation',
 'along',
 'way',
 'get',

In [57]:
len(wv.index_to_key)

3000000

In [54]:
wv[words[0][2]]

array([ 5.98144531e-02,  2.38037109e-02,  6.73828125e-02,  3.16406250e-01,
       -1.89453125e-01,  1.64794922e-02,  1.53320312e-01,  2.52685547e-02,
        1.07910156e-01, -1.75781250e-02, -1.07421875e-01, -4.29687500e-02,
       -1.09863281e-01,  6.13403320e-03,  3.12500000e-02, -5.32226562e-02,
        6.93359375e-02,  2.04101562e-01,  2.35595703e-02, -9.03320312e-02,
       -7.03125000e-02, -6.64062500e-02,  7.27539062e-02, -4.80957031e-02,
        6.10351562e-03, -1.19628906e-01, -1.30859375e-01,  8.10546875e-02,
       -1.26953125e-01,  1.60156250e-01,  6.22558594e-02,  1.08642578e-02,
       -3.11279297e-02,  8.23974609e-03, -1.00585938e-01, -9.99450684e-04,
        1.35742188e-01, -6.07910156e-02,  1.42211914e-02, -1.40625000e-01,
        6.78710938e-02, -6.25000000e-02,  9.42382812e-02, -9.61914062e-02,
        1.10839844e-01, -1.97753906e-02, -2.31933594e-03,  1.75781250e-01,
        3.56445312e-02, -3.06640625e-01, -1.34765625e-01,  1.23046875e-01,
       -7.86132812e-02,  

In [59]:
def avg_word2vec(doc):
    # Filter out words not in the model's vocabulary
    valid_words = [word for word in doc if word in wv.index_to_key]
    
    # If there are no valid words, return a zero vector
    if not valid_words:
        return np.zeros(wv.vector_size)
    
    # Compute the mean vector
    return np.mean([wv[word] for word in valid_words], axis=0)

In [61]:
from tqdm import tqdm

In [62]:
#apply for the entire sentences
import numpy as np
X=[]
for i in tqdm(range(len(words))):
    X.append(avg_word2vec(words[i]))

100%|██████████| 12000/12000 [13:53<00:00, 14.39it/s]


In [63]:
X

[array([ 8.69389772e-02,  5.56045137e-02, -6.62555778e-03,  5.49082085e-02,
        -4.81407791e-02,  2.41103005e-02,  3.84673774e-02, -7.23202303e-02,
         8.35768059e-02,  8.45640078e-02,  3.17761414e-02, -1.23053476e-01,
        -2.92842165e-02,  3.17570344e-02, -1.09667338e-01,  7.24112391e-02,
         3.42744961e-02,  1.09130919e-01,  2.19011195e-02, -7.30251968e-02,
        -8.05165444e-04,  4.38739769e-02,  4.29814942e-02, -1.52631039e-02,
         3.64519209e-02, -6.48518652e-02, -7.08713010e-02,  6.56648576e-02,
         6.27509505e-02, -3.48373242e-02, -1.91186555e-02,  1.28032956e-02,
        -2.04546917e-02,  2.09696591e-02,  1.06585966e-02, -9.98429168e-05,
         8.11691284e-02, -2.52961870e-02,  1.94963031e-02,  9.20157284e-02,
         9.09672529e-02, -6.99274316e-02,  1.18189409e-01, -1.96890384e-02,
        -1.21319089e-02, -3.37725505e-02, -4.54336293e-02,  6.43419428e-03,
         2.34758761e-02,  1.96744651e-02, -5.10927662e-02,  3.53634357e-02,
        -8.6

In [64]:
##independent Features
X_new=np.array(X)

In [66]:
X_new.shape

(12000, 300)

In [69]:
## Dependent Features
## Output Features
y = df[list(map(lambda x: len(x)>0 ,corpus))]
y=pd.get_dummies(df['rating'])
y=y.iloc[:,0].values

In [70]:
y

array([False, False, False, ..., False,  True, False])

In [71]:
len(y)

12000

In [72]:
X_new

array([[ 0.08693898,  0.05560451, -0.00662556, ..., -0.06590405,
         0.03220699,  0.0127058 ],
       [ 0.05125427,  0.04479302, -0.01989894, ..., -0.04082065,
        -0.00518523, -0.03397496],
       [ 0.03286018,  0.01291046, -0.01148453, ..., -0.00937195,
        -0.00501766, -0.02010117],
       ...,
       [ 0.05172624,  0.02350485, -0.03404709, ..., -0.04426101,
        -0.00892376,  0.03046312],
       [ 0.10197096,  0.0168457 ,  0.06023701, ..., -0.06298828,
         0.0067796 ,  0.04958872],
       [ 0.04285516,  0.03177579, -0.00589441, ..., -0.07430465,
         0.01875545, -0.00389396]], dtype=float32)

In [73]:
## this is the final independent features
df1=pd.DataFrame()
for i in range(0,len(X_new)):
    row_df = pd.DataFrame(X_new[i].reshape(1, -1))
    df1=pd.concat([df1,row_df],ignore_index=True)


df1
    

0         1         2         3         4         5         6    \
0      0.086939  0.055605 -0.006626  0.054908 -0.048141  0.024110  0.038467   
1      0.051254  0.044793 -0.019899  0.090773 -0.030171 -0.066038  0.054843   
2      0.032860  0.012910 -0.011485  0.084149 -0.058038  0.003719  0.005551   
3      0.098432  0.020602  0.020909  0.081812 -0.055579  0.044883  0.121294   
4      0.042953  0.053492 -0.037432  0.141052 -0.001160 -0.030052  0.145020   
...         ...       ...       ...       ...       ...       ...       ...   
11995  0.104171 -0.032914  0.003977  0.111535 -0.093178  0.128453  0.010247   
11996  0.026680  0.029347 -0.022180  0.072583  0.020484  0.030239  0.064881   
11997  0.051726  0.023505 -0.034047  0.116282 -0.041782 -0.030528  0.016802   
11998  0.101971  0.016846  0.060237  0.071571 -0.109396  0.035844  0.056171   
11999  0.042855  0.031776 -0.005894  0.076215 -0.059401  0.001439  0.055222   

            7         8         9    ...       290       291       292  \
0     -0.072320  0.083577  0.084564  ... -0.061049  0.038379 -0.106497   
1     -0.035899  0.053366  0.101480  ... -0.053123  0.056960 -0.087101   
2     -0.071625  0.087841  0.043651  ... -0.051870  0.057238 -0.104562   
3      0.015328  0.054985  0.082101  ... -0.118694 -0.003322 -0.089382   
4      0.000656  0.084297  0.040771  ... -0.036285  0.038158 -0.070282   
...         ...       ...       ...  ...       ...       ...       ...   
11995 -0.074180  0.108033  0.040026  ... -0.010813  0.094368 -0.185505   
11996 -0.041849  0.064111  0.063710  ... -0.093097 -0.007488 -0.089578   
11997 -0.041708  0.085683  0.061633  ...  0.011770  0.067967 -0.132215   
11998 -0.054830  0.036771 -0.001377  ... -0.038473  0.094457 -0.072256   
11999 -0.060860  0.101573  0.040263  ... -0.134460  0.044709 -0.091135   

            293       294       295       296       297       298       299  
0     -0.000109 -0.057955 -0.032478  0.014949 -0.065904  0.032207  0.012706  
1      0.021264 -0.082894 -0.036609  0.030698 -0.040821 -0.005185 -0.033975  
2     -0.020693 -0.000588 -0.036937 -0.001410 -0.009372 -0.005018 -0.020101  
3      0.011739 -0.067574 -0.091642  0.011637 -0.044886  0.029240  0.040308  
4      0.000774  0.108490 -0.028992  0.062061  0.017662  0.054092 -0.048580  
...         ...       ...       ...       ...       ...       ...       ...  
11995 -0.049731 -0.055401 -0.021253  0.112020  0.023544  0.002166  0.132721  
11996 -0.051892 -0.035436 -0.065701  0.021214 -0.047163  0.007931 -0.046689  
11997  0.008680 -0.080632 -0.042657  0.049070 -0.044261 -0.008924  0.030463  
11998  0.043762 -0.024010  0.002693  0.010667 -0.062988  0.006780  0.049589  
11999  0.032505 -0.072509 -0.028654  0.039984 -0.074305  0.018755 -0.003894  

[12000 rows x 300 columns]

In [75]:
df1.isnull().sum()

0      0
1      0
2      0
3      0
4      0
      ..
295    0
296    0
297    0
298    0
299    0
Length: 300, dtype: int64

In [76]:
## Train Test Split
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(df1,y,test_size=0.20)

In [77]:
X_train

0         1         2         3         4         5         6    \
774   0.067013 -0.006200 -0.009490  0.128084 -0.124660  0.121685  0.045352   
5880  0.080827 -0.024129 -0.083594  0.101009 -0.087492 -0.032149 -0.004355   
7445  0.140044  0.022090 -0.040118  0.061910 -0.071340  0.170898  0.044970   
9932  0.061791  0.012151 -0.004561  0.106456 -0.028542 -0.007080  0.066502   
3962  0.114301 -0.007808 -0.010345  0.193397 -0.039557  0.044621  0.116230   
...        ...       ...       ...       ...       ...       ...       ...   
6850  0.110269 -0.011742 -0.012801  0.083658 -0.040818  0.008837  0.109144   
680   0.049500  0.026139 -0.035007  0.100833 -0.042532 -0.007845  0.079698   
4089  0.037327  0.050616  0.028156  0.095552 -0.001124 -0.016533  0.093488   
5231  0.061488  0.023881 -0.007214  0.088902 -0.052154  0.003413  0.050832   
3110  0.154598 -0.029843 -0.070040  0.086196 -0.079860 -0.000639  0.066841   

           7         8         9    ...       290       291       292  \
774  -0.010230  0.085208  0.071672  ... -0.028783  0.132851 -0.106941   
5880 -0.112970  0.048014  0.131868  ... -0.043245  0.042655 -0.082302   
7445 -0.020312  0.004522  0.003423  ... -0.019267  0.012032 -0.049797   
9932 -0.042699  0.044178  0.020355  ... -0.063463 -0.005266 -0.082348   
3962 -0.011569  0.065563  0.059630  ... -0.005208  0.086226 -0.106999   
...        ...       ...       ...  ...       ...       ...       ...   
6850 -0.001597  0.105569  0.060395  ... -0.044002  0.005140 -0.090022   
680  -0.051336  0.089174  0.095213  ... -0.056237  0.110706 -0.121135   
4089  0.005128  0.045197  0.064136  ... -0.042541  0.055240 -0.128445   
5231  0.005654  0.060164  0.066314  ... -0.057995  0.056758 -0.080302   
3110 -0.010599  0.045915  0.040316  ... -0.023093  0.075102 -0.070083   

           293       294       295       296       297       298       299  
774   0.012538 -0.153503 -0.067174  0.022005 -0.079241 -0.002419  0.039056  
5880  0.014828 -0.121928 -0.088395  0.102393 -0.080778 -0.031691  0.058793  
7445 -0.080546 -0.004700 -0.159770  0.016356  0.051637 -0.026164  0.013385  
9932  0.012033 -0.008187 -0.088673  0.015688 -0.028858  0.009188 -0.002810  
3962  0.041147 -0.041415 -0.029072  0.018381 -0.052378 -0.054082 -0.035238  
...        ...       ...       ...       ...       ...       ...       ...  
6850 -0.003347 -0.037939 -0.051162  0.037612 -0.088557 -0.004816  0.011015  
680   0.066148 -0.040601 -0.010944  0.040207 -0.069437 -0.011399 -0.051354  
4089  0.028651 -0.081281 -0.048817 -0.006161 -0.015829 -0.061653 -0.013671  
5231  0.007523 -0.046637 -0.057789  0.052347 -0.071549 -0.028859  0.004037  
3110 -0.063819 -0.052296 -0.104945  0.030740 -0.099868  0.029074  0.014844  

[9600 rows x 300 columns]

In [79]:
from sklearn.ensemble import RandomForestClassifier
classifier=RandomForestClassifier()

In [80]:
classifier.fit(X_train,y_train)

RandomForestClassifier()

In [81]:
y_pred=classifier.predict(X_test)

In [82]:
from sklearn.metrics import accuracy_score,classification_report
print(accuracy_score(y_test,y_pred))

0.7775


In [83]:
print(classification_report(y_test,y_pred))

              precision    recall  f1-score   support

       False       0.77      0.95      0.85      1601
        True       0.80      0.44      0.57       799

    accuracy                           0.78      2400
   macro avg       0.79      0.69      0.71      2400
weighted avg       0.78      0.78      0.76      2400

